<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Digital-Referrals" data-toc-modified-id="Digital-Referrals-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Digital Referrals</a></span></li><li><span><a href="#HIVST-Assessments" data-toc-modified-id="HIVST-Assessments-2"><span class="toc-item-num">2&nbsp;&nbsp;</span>HIVST Assessments</a></span></li></ul></div>

In [1]:
%run "../../xUtilz/utilz_only_loader.ipynb"

<IPython.core.display.Javascript object>

In [2]:
db = pd.read_excel( "../../datasets/LG/IN/181114-IN Data.xlsx", sheetname="Digital Referral(Most recent)" )
dbh = pd.read_excel( "../../datasets/LG/IN/181114-IN Data.xlsx", sheetname="HIVST" )

#db.head().T
#dbh.head().T

In [3]:
db["chv_name"] = "CHV " +  pd.Series( pd.factorize( db["chv_name"])[0] + 1).astype( str)
db["patient_name"] = "Patient " +  pd.Series( pd.factorize( db["patient_name"])[0] + 1).astype( str)
db.drop( "chv_phone", axis=1, inplace=True)
db.drop( 'month', axis=1, inplace=True)

dbh["chv_name"] = "CHV " +  pd.Series( pd.factorize( dbh["chv_name"])[0] + 1).astype( str)
dbh["patient_name"] = "Patient " +  pd.Series( pd.factorize( dbh["patient_name"])[0] + 1).astype( str)
dbh.drop( "chv_phone", axis=1, inplace=True)

In [4]:
reasons_groupz = { 
    "Neonates" : [ "months", "umbilical", "umbllical"], 
    "Pregnancy" : ["delivery"], 
    "U5 Danger Signs" : [ "Danger", "Diarrhoea", "Diarrhea", "Dairrhea", "Coughing", "Cough", "Fever","Pneumonia", "Pnuemonia",
                        "Pheumonia", ],
    "HIVST Refer" : ["reactive", "partner", "intimate"], 
    "HIVST Ed" : ["HIVST_Assessed", ], 
    "Unsupported Cases" : []
}

## digital referrals 
db["Category Referral Reason"] = db["reason_for_referral"].apply( lambda x: searchString(x, reasons_groupz) ) 

## HIVST assessments 
dbh["health_facility"][ dbh["health_facility"] == "[NULL]" ] =  "Assessment Only"
dbh["reason_for_referral"][ dbh["reason_for_referral"] == "[NULL]" ] =  "HIVST_Assessed" #pd.isnull(dbh["reason_for_referral"])
dbh["Category Referral Reason"] = dbh["reason_for_referral"].apply( lambda x: searchString(x, reasons_groupz) ) 
# shorter descriptions for referral reasons HIVST TODO: refactor regex grep
dbh["reason_for_referral"][ dbh["reason_for_referral"] == "CHV referral: reactive or non-disclose" ] =  "Reactive/non-disclose"
dbh["reason_for_referral"][ dbh["reason_for_referral"] == "Intimate partner violence case" ] =  "IPV case"
dbh["reason_for_referral"][ dbh["reason_for_referral"] == "CHV referral: reactive or non-discloseInvalid test" ] =  "Invalid test"

var_bucket_reasons =  "Category Referral Reason"
var_all_reasons = "All"
var_Unsupported = "Unsupported Cases"
var_HIVST = "HIVST Refer"
var_HIVST_ED = "HIVST Ed"
var_Display_Colz = ["reported_date", "chv_name", "patient_name" ,"reason_for_referral", var_bucket_reasons]

#dbh.sample( 5).T

In [5]:
# 1. set Date of referral to a datetime type 
#db["reported_date"] = pd.to_datetime( db["reported_date"], format="%d-%b-%y") # inplace=True)
db["reported_date"] = pd.to_datetime( db["reported_date"], format="%Y-%b-%d %H:%M:%S") 

# 2. Extract Month and year categories 
db["Year"] = db["reported_date"].dt.year 
db["Month"] = db["reported_date"].dt.strftime('%b-%y') 
db["Day_of_Week"] = db["reported_date"].dt.weekday_name.str[:3] 

db.sort_values( by='reported_date', inplace=True)

LAST_UPDATED = db["reported_date"].max().strftime( '%d-%b-%Y')


# 1. set Date of referral to a datetime type 
dbh["reported_date"] = pd.to_datetime( dbh["reported_date"], format="%Y-%b-%d %H:%M:%S") 

# 2. Extract Month and year categories 
dbh["Year"] = dbh["reported_date"].dt.year 
dbh["Month"] = dbh["reported_date"].dt.strftime('%b-%y') 
dbh["Day_of_Week"] = dbh["reported_date"].dt.weekday_name.str[:3] 

dbh.sort_values( by='reported_date', inplace=True)

LAST_UPDATED_HIVST  = db["reported_date"].max().strftime( '%d-%b-%Y')


#db.head().T
#dbh.head().T

In [16]:
### plot them

def plot_counts_bar(df, t, col, order=None):
    ax = sns.countplot( data=df, x=col, order=order ) 
    # set % 
    total = len( df )
    for p in ax.patches:
        height = p.get_height()
        if not( pd.isnull(height) ):        
            ax.text(p.get_x()+p.get_width()/2.,
                height + 0.1,
                '{:1.0f} %'.format(height/total*100),
                ha="center") 

    ax.set_title( t ) ;  
    return ax
 

def plot_bar_reasons(df, t):
    return plot_counts_bar(df, t, var_bucket_reasons , df[var_bucket_reasons].value_counts().index) 


def plot_bar_timing(df, t):
    return plot_counts_bar(df, t, "Day_of_Week", ["Sun", "Mon", "Tue", "Wed", "Thu", "Fri", "Sat"] ) 


def plot_word_cloud( df, t ):
    stop_words = STOPWORDS.union( ["CHV", "referral" ] )
    ## Translating Swahili to Eng 
    plt.imshow( WordCloud( 
        background_color="white", 
        max_font_size=50, 
        max_words=200, 
        stopwords=stop_words,
    ).generate( " ".join( df["reason_for_referral"].fillna('No_Input') ) ) , 
               interpolation='bilinear'  )
    plt.axis( "off" )
    plt.title( t )

def plot_timeline( df, t):
    myFmt = DateFormatter("%d-%b") 
    
    #ax = sns.countplot( data=df, x="Date of referral" ) 
    ax = df['reported_date'].value_counts().sort_index().plot.line()
    ax.set_title( t )  
    ax.xaxis_date( )
    ax.xaxis.set_minor_locator(WeekdayLocator(byweekday=MO)) ## intended 
    ax.xaxis.set_major_locator( WeekdayLocator(byweekday=MO, interval=1) ) ## only label at every 4th week 
    #ax.xaxis.set_major_formatter( DateFormatter('%H:%M:') )
    ax.xaxis.set_major_formatter( myFmt)
    return ax

### TBD refactor all below to

def plot_hivst_reasons(df, t):
    return plot_counts_bar(df[ df["reason_for_referral"] != 'HIVST_Assessed'], t, "reason_for_referral" ) 


def plot_hf_actvity( df, t):
    return plot_counts_bar(df, t, "health_facility")

def plot_hf_confirmation( df, t):
    return plot_counts_bar(df, t, "health_facility_confirmation") 

def plot_monthly_counts(df, t):
    return plot_counts_bar(df, t, "Month") 



### Digital Referrals

In [7]:
display(HTML('<b>Last Updated: %s</b>'%LAST_UPDATED))

In [8]:
display(HTML('<b>Number of Records Table - Digital Referrals </b>'))
t = pd.pivot_table( db, index=var_bucket_reasons, values=["referral_uuid"], aggfunc='count', margins=True ).T
t["Total Per. CHV"] = len( db ) / len( db.chv_name.unique() )
t[ "Total per CHV per Month"] = (len( db ) / len( db.chv_name.unique() ) )/ (db.reported_date.max().to_period('M') - db.reported_date.min().to_period('M'))
t['Number of CHVs'] =  len( db.chv_name.unique() ) 
t['Records per Client'] =  len(db)/len( db.patient_name.unique() )
t.round(2)

Category Referral Reason  HIVST Refer  Neonates  No Response  Pregnancy  \
referral_uuid                    19.0       7.0         11.0        1.0   

Category Referral Reason  U5 Danger Signs  Unsupported Cases    All  \
referral_uuid                        43.0               54.0  135.0   

Category Referral Reason  Total Per. CHV  Total per CHV per Month  \
referral_uuid                        5.4                      1.8   

Category Referral Reason  Number of CHVs  Records per Client  
referral_uuid                         25                1.14

In [9]:
## Options List = referral reasons/types 
options_list = [ var_all_reasons] + db[var_bucket_reasons].unique().tolist()
#print( options_list )

@interact( referral_reasons=options_list) #, style = {'description_width': 'initial'})
def plot_by( referral_reasons): 
    if( referral_reasons == var_all_reasons):
        df = db
    else:
        df = db[ db[var_bucket_reasons] == referral_reasons ] 
    
    title = '%s Reasons - %s'% (referral_reasons, LAST_UPDATED )
    title_all = '%s Reasons - %s'% (var_all_reasons, LAST_UPDATED )
    title_unsupported = '%s Reasons - %s'% (var_Unsupported, LAST_UPDATED )
    title_HIVST = '%s Reasons - %s'% (var_HIVST, LAST_UPDATED )
    title_timing = 'Timing: %s Referrals - %s' % (referral_reasons, LAST_UPDATED )

    #f, a = plt.subplots( nrows=2, ncols=3, figsize=(20,15) )

    plt.figure(figsize=(25,20))
    grid = plt.GridSpec( 3, 3, wspace=0.4, hspace=0.3)

    plt.subplot( grid[0,0] )
    plot_bar_reasons(db, title_all )

    plt.subplot( grid[0,1] )
    plot_bar_timing( df, title_timing)

    ## HF Activity 
    plt.subplot( grid[0,2] )
    plot_hf_actvity(df, "HF - "+title)

    ## unsupported cases only
    plt.subplot( grid[1,0] )
    plot_word_cloud( db[ (db[var_bucket_reasons]!= var_HIVST) & (db[var_bucket_reasons] == var_Unsupported)] , title_unsupported)

    ## word cloud all cases - no HIVST by default b/c not user entered 
    plt.subplot( grid[1,1] )
    plot_word_cloud( df if referral_reasons == var_HIVST else df[df[var_bucket_reasons]!=var_HIVST], "Referral Reasons - "+referral_reasons)
    #plot_word_cloud(db, 'Referral Reasons')
    
    ## 
    plt.subplot( grid[1,2])
    plot_counts_bar(df, "Unconfirmed - "+title, "unconfirmed")

    ## monthly counts
    plt.subplot( grid[2,0] )
    plot_monthly_counts( df, title_all)
    
    ## timeline
    plt.subplot( grid[2,1:] )
    plot_timeline( df, title_all)

    plt.tight_layout() 
        

#interact( plot_by, group_by=options_list);

interactive(children=(Dropdown(description='referral_reasons', options=('All', 'Unsupported Cases', 'U5 Danger…

### HIVST Assessments

In [10]:
display(HTML('<b>Last Updated: %s</b>'%LAST_UPDATED_HIVST))
#print("")

In [11]:
display(HTML('<b>Number of records Table - HIVST Assessments</b>'))
t = pd.pivot_table( dbh, index="health_facility", values=["hivst_enrollment_uuid"], aggfunc='count', margins=True ).T
t["Total Per. CHV"] = len( dbh ) / len( dbh.chv_name.unique() )
t[ "Total per CHV per Month"] = (len( dbh ) / len( dbh.chv_name.unique() ) )/ (dbh.reported_date.max().to_period('M') - dbh.reported_date.min().to_period('M'))
t['Number of CHVs'] =  len( dbh.chv_name.unique() ) 
t['Records per Client'] =  len(dbh)/len( dbh.patient_name.unique() )
t.round(2)

health_facility        Assessment Only  gucha  keragia   All  Total Per. CHV  \
hivst_enrollment_uuid             74.0   15.0      4.0  93.0             6.2   

health_facility        Total per CHV per Month  Number of CHVs  \
hivst_enrollment_uuid                      6.2              15   

health_facility        Records per Client  
hivst_enrollment_uuid                1.02

In [17]:
## options list = health facilities or CU
options_list = [var_all_reasons] + dbh.health_facility.unique().tolist()
var_bucket_unit = "health_facility"

@interact( unit=options_list) #, style = {'description_width': 'initial'})
def plot_by( unit ): 
    if( unit == var_all_reasons):
        df = dbh
    else:
        df = dbh[ dbh[var_bucket_unit] == unit ] 
    
    title = '%s - %s'% (unit, LAST_UPDATED_HIVST ) 
    title_timing = 'Timing: %s Referrals - %s' % (unit, LAST_UPDATED_HIVST )

    
    plt.figure(figsize=(25,20))
    grid = plt.GridSpec( 2, 3, wspace=0.4, hspace=0.3)

    ## HIVST assessment numbers
    plt.subplot( grid[0,0] )
    plot_bar_reasons(df, "Records: "+title )

    ## HIVST referral reasons 
    plt.subplot( grid[0,1] )
    plot_hivst_reasons( df, "Referral Reasons: "+title )

    ## HIVST assessment timing
    plt.subplot( grid[0,2] )    
    plot_bar_timing( df, title_timing)
    

    ## IPV cases 
    plt.subplot( grid[1,0] )
    plot_counts_bar(df, "IPV: "+title, "is_ipv_case")

    ## completed enrollment - catchment issue 
    plt.subplot( grid[1,1] )    
    plot_counts_bar(df, "Catchment??: "+title, "completed_enrollment")
    
    ## require f/u OR eligible retake
    #plt.subplot( grid[1,2])
    #plot_counts_bar(df, "Eligble Retake: "+title, "eligible_for_retake")

    ## first timers
    plt.subplot( grid[1,2])
    plot_counts_bar(df, "First_Timers: "+title, "first_time_tester")

    plt.tight_layout() 
        

#interact( plot_by, group_by=options_list);

interactive(children=(Dropdown(description='unit', options=('All', 'Assessment Only', 'gucha', 'keragia'), val…